# Interactive Dashboard Python

### NOTES
#### Panel is an open-source Python library that lets you create custom interactive web apps and dashboards by connecting user-defined widgets to plots, images, tables, or text.

#### Panel can be used with many data visualization modules.

#### Most plots and maps in this tutorial have an interactive option (zoom, hover, etc.).

#### A common pattern to create a widget, interactive plot, or basic dashboard is to create the widget(s), then create the functions that will be used, then create the interaction between the widgets and functions using interact or layout (or similar).

In [1]:
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
import panel as pn
import geopandas
import hvplot.pandas
from datetime import datetime
import folium
from panel.interact import interact
pn.extension()
pn.extension('tabulator')



## loading the suicide info data

In [2]:
# cache data to improve dashboard performance
if 'data' not in pn.state.cache.keys():
    df = pd.read_csv('./master.csv')
    pn.state.cache['data'] = df.copy()
else: 
    df = pn.state.cache['data']

In [3]:
df.head()

country  year     sex          age  suicides_no  population  \
0  Albania  1987    male  15-24 years           21      312900   
1  Albania  1987    male  35-54 years           16      308000   
2  Albania  1987  female  15-24 years           14      289700   
3  Albania  1987    male    75+ years            1       21800   
4  Albania  1987    male  25-34 years            9      274300   

   suicides/100k pop country-year  HDI for year  gdp_for_year ($)   \
0               6.71  Albania1987           NaN      2,156,624,900   
1               5.19  Albania1987           NaN      2,156,624,900   
2               4.83  Albania1987           NaN      2,156,624,900   
3               4.59  Albania1987           NaN      2,156,624,900   
4               3.28  Albania1987           NaN      2,156,624,900   

   gdp_per_capita ($)       generation  
0                 796     Generation X  
1                 796           Silent  
2                 796     Generation X  
3                 796  G.I. Generation  
4                 796          Boomers

In [4]:
df.nunique()

country                 101
year                     32
sex                       2
age                       6
suicides_no            2084
population            25564
suicides/100k pop      5298
country-year           2321
HDI for year            305
 gdp_for_year ($)      2321
gdp_per_capita ($)     2233
generation                6
dtype: int64

In [5]:
df.country.value_counts()

Mauritius                 382
Iceland                   382
Austria                   382
Netherlands               382
Japan                     372
                         ... 
Bosnia and Herzegovina     24
Cabo Verde                 12
Macau                      12
Dominica                   12
Mongolia                   10
Name: country, Length: 101, dtype: int64

In [6]:
df.isna().sum()

country                   0
year                      0
sex                       0
age                       0
suicides_no               0
population                0
suicides/100k pop         0
country-year              0
HDI for year          19456
 gdp_for_year ($)         0
gdp_per_capita ($)        0
generation                0
dtype: int64

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27820 entries, 0 to 27819
Data columns (total 12 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   country             27820 non-null  object 
 1   year                27820 non-null  int64  
 2   sex                 27820 non-null  object 
 3   age                 27820 non-null  object 
 4   suicides_no         27820 non-null  int64  
 5   population          27820 non-null  int64  
 6   suicides/100k pop   27820 non-null  float64
 7   country-year        27820 non-null  object 
 8   HDI for year        8364 non-null   float64
 9    gdp_for_year ($)   27820 non-null  object 
 10  gdp_per_capita ($)  27820 non-null  int64  
 11  generation          27820 non-null  object 
dtypes: float64(2), int64(4), object(6)
memory usage: 2.5+ MB


In [8]:
# Make DataFrame Pipeline Interactive
idf = df.interactive()

In [9]:
# Define Panel widgets
year_slider = pn.widgets.IntSlider(name='Year slider', start=1985, end=2016, step=2, value=2000,tooltips=True)
year_slider

IntSlider(end=2016, name='Year slider', start=1985, step=2, value=2000)

## world stats

#### Some minor data preprocessing

In [10]:
df[' gdp_for_year ($) ']=df[' gdp_for_year ($) '].str.replace(',','').astype(str).astype(int)

In [11]:
df.head(2)

country  year   sex          age  suicides_no  population  \
0  Albania  1987  male  15-24 years           21      312900   
1  Albania  1987  male  35-54 years           16      308000   

   suicides/100k pop country-year  HDI for year   gdp_for_year ($)   \
0               6.71  Albania1987           NaN          2156624900   
1               5.19  Albania1987           NaN          2156624900   

   gdp_per_capita ($)    generation  
0                 796  Generation X  
1                 796        Silent

In [12]:
year_level_agg=df.pivot_table(index='year',values=['suicides_no','population',' gdp_for_year ($) '],aggfunc={'suicides_no':sum,'population':sum,' gdp_for_year ($) ':sum}).reset_index()
year_level_agg.head()

year   gdp_for_year ($)   population  suicides_no
0  1985     110964754234500  1008600086       116063
1  1986     132609631982868  1029909613       120670
2  1987     155769882274200  1095029726       126842
3  1988     175557691204476  1054094424       121026
4  1989     191618261647176  1225514347       160244

In [13]:
year_level_agg['suicides per 100k people']=np.round(year_level_agg['suicides_no']*100000/year_level_agg['population'],2)

In [14]:
year_level_agg['gdp per capita($)']=np.round((year_level_agg[' gdp_for_year ($) ']/year_level_agg['population']).astype(float),0)

In [15]:
year_level_agg.head()

year   gdp_for_year ($)   population  suicides_no  \
0  1985     110964754234500  1008600086       116063   
1  1986     132609631982868  1029909613       120670   
2  1987     155769882274200  1095029726       126842   
3  1988     175557691204476  1054094424       121026   
4  1989     191618261647176  1225514347       160244   

   suicides per 100k people  gdp per capita($)  
0                     11.51           110019.0  
1                     11.72           128759.0  
2                     11.58           142252.0  
3                     11.48           166548.0  
4                     13.08           156357.0

In [16]:
year_level_agg.dtypes

year                          int64
 gdp_for_year ($)             int64
population                    int64
suicides_no                   int64
suicides per 100k people    float64
gdp per capita($)           float64
dtype: object

In [17]:
iyear_level_agg = year_level_agg.interactive()

In [18]:
# Radio buttons for suicide rate measures
yaxis_year_world = pn.widgets.RadioButtonGroup(
    name='Y axis', 
    options=['suicides per 100k people', 'gdp per capita($)'],
    button_type='success'
)
world_year_pipeline = (
    iyear_level_agg[
        (iyear_level_agg.year <= year_slider)
    ]
    .groupby(['year'])[yaxis_year_world].mean()
    .to_frame()
    .reset_index()
    .sort_values(by=['year'])  
    .reset_index(drop=True)
)


In [19]:
world_year_pipeline_plot = world_year_pipeline.hvplot(x = 'year', y=yaxis_year_world,line_width=2, title="Worldwide Suicides & GDP per Capita by Year"
                                                     ,width=800,height=400)
world_year_pipeline_plot

#### Year-Gender view

In [20]:
year_gender_level_agg=df.pivot_table(index=['year','sex'],values=['suicides_no','population',' gdp_for_year ($) '],aggfunc={'suicides_no':sum,'population':sum,' gdp_for_year ($) ':sum}).reset_index()
year_gender_level_agg.head()

year     sex   gdp_for_year ($)   population  suicides_no
0  1985  female      55482377117250   513013055        32479
1  1985    male      55482377117250   495587031        83584
2  1986  female      66304815991434   524465866        33852
3  1986    male      66304815991434   505443747        86818
4  1987  female      77884941137100   559183789        35006

In [21]:
year_gender_level_agg['suicides per 100k people']=np.round(year_gender_level_agg['suicides_no']*100000/year_gender_level_agg['population'],2)

year_gender_level_agg['gdp per capita($)']=np.round((year_gender_level_agg[' gdp_for_year ($) ']/year_gender_level_agg['population']).astype(float),0)

print(year_gender_level_agg.head())

print(year_gender_level_agg.dtypes)

   year     sex   gdp_for_year ($)   population  suicides_no  \
0  1985  female      55482377117250   513013055        32479   
1  1985    male      55482377117250   495587031        83584   
2  1986  female      66304815991434   524465866        33852   
3  1986    male      66304815991434   505443747        86818   
4  1987  female      77884941137100   559183789        35006   

   suicides per 100k people  gdp per capita($)  
0                      6.33           108150.0  
1                     16.87           111953.0  
2                      6.45           126424.0  
3                     17.18           131181.0  
4                      6.26           139283.0  
year                          int64
sex                          object
 gdp_for_year ($)             int64
population                    int64
suicides_no                   int64
suicides per 100k people    float64
gdp per capita($)           float64
dtype: object


In [22]:
iyear_gender_level_agg = year_gender_level_agg.interactive()

In [23]:
world_year_gender_pipeline = (
    iyear_gender_level_agg[
        (iyear_gender_level_agg.year <= year_slider)
    ]
    .groupby(['year','sex'])[yaxis_year_world].mean()
    .to_frame()
    .reset_index()
    .sort_values(by=['year','sex'])  
    .reset_index(drop=True)
)



In [24]:
world_year_gender_pipeline = world_year_gender_pipeline.hvplot(x = 'year',by='sex', y=yaxis_year_world,line_width=2, title="Worldwide Suicides & GDP per Capita by Gender-Year",width=800,height=400,legend='top')
world_year_gender_pipeline

#### Year-Age view

In [25]:
year_age_level_agg=df.pivot_table(index=['year','age'],values=['suicides_no','population',' gdp_for_year ($) '],aggfunc={'suicides_no':sum,'population':sum,' gdp_for_year ($) ':sum}).reset_index()
year_age_level_agg.head()

year          age   gdp_for_year ($)   population  suicides_no
0  1985  15-24 years      18494125705750   196974439        17870
1  1985  25-34 years      18494125705750   173536624        20771
2  1985  35-54 years      18494125705750   246046628        35748
3  1985   5-14 years      18494125705750   199192522          984
4  1985  55-74 years      18494125705750   152769432        28736

In [26]:
year_age_level_agg['suicides per 100k people']=np.round(year_age_level_agg['suicides_no']*100000/year_age_level_agg['population'],2)

year_age_level_agg['gdp per capita($)']=np.round((year_age_level_agg[' gdp_for_year ($) ']/year_age_level_agg['population']).astype(float),0)

print(year_age_level_agg.head())

print(year_age_level_agg.dtypes)

iyear_age_level_agg = year_age_level_agg.interactive()

   year          age   gdp_for_year ($)   population  suicides_no  \
0  1985  15-24 years      18494125705750   196974439        17870   
1  1985  25-34 years      18494125705750   173536624        20771   
2  1985  35-54 years      18494125705750   246046628        35748   
3  1985   5-14 years      18494125705750   199192522          984   
4  1985  55-74 years      18494125705750   152769432        28736   

   suicides per 100k people  gdp per capita($)  
0                      9.07            93891.0  
1                     11.97           106572.0  
2                     14.53            75165.0  
3                      0.49            92845.0  
4                     18.81           121059.0  
year                          int64
age                          object
 gdp_for_year ($)             int64
population                    int64
suicides_no                   int64
suicides per 100k people    float64
gdp per capita($)           float64
dtype: object


In [27]:
world_year_age_pipeline = (
    iyear_age_level_agg[
        (iyear_age_level_agg.year <= year_slider)
    ]
    .groupby(['year','age'])[yaxis_year_world].mean()
    .to_frame()
    .reset_index()
    .sort_values(by=['year','age'])  
    .reset_index(drop=True)
)



In [28]:
world_year_age_pipeline = world_year_age_pipeline.hvplot(x = 'year',by='age', y=yaxis_year_world,line_width=2, title="Worldwide Suicides & GDP per Capita by Age-Year",width=800,height=400,legend='top')
world_year_age_pipeline

## country level view

In [29]:
### reading country level data from geopandas for country boundaries
world = geopandas.read_file(geopandas.datasets.get_path("naturalearth_lowres"))
print("Geometry Column Name : ", world.geometry.name)
print("Dataset Size : ", world.shape)
world.head()

Geometry Column Name :  geometry
Dataset Size :  (177, 6)


pop_est      continent                      name iso_a3  gdp_md_est  \
0     920938        Oceania                      Fiji    FJI      8374.0   
1   53950935         Africa                  Tanzania    TZA    150600.0   
2     603253         Africa                 W. Sahara    ESH       906.5   
3   35623680  North America                    Canada    CAN   1674000.0   
4  326625791  North America  United States of America    USA  18560000.0   

                                            geometry  
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...

In [30]:
world['name'].unique()

array(['Fiji', 'Tanzania', 'W. Sahara', 'Canada',
       'United States of America', 'Kazakhstan', 'Uzbekistan',
       'Papua New Guinea', 'Indonesia', 'Argentina', 'Chile',
       'Dem. Rep. Congo', 'Somalia', 'Kenya', 'Sudan', 'Chad', 'Haiti',
       'Dominican Rep.', 'Russia', 'Bahamas', 'Falkland Is.', 'Norway',
       'Greenland', 'Fr. S. Antarctic Lands', 'Timor-Leste',
       'South Africa', 'Lesotho', 'Mexico', 'Uruguay', 'Brazil',
       'Bolivia', 'Peru', 'Colombia', 'Panama', 'Costa Rica', 'Nicaragua',
       'Honduras', 'El Salvador', 'Guatemala', 'Belize', 'Venezuela',
       'Guyana', 'Suriname', 'France', 'Ecuador', 'Puerto Rico',
       'Jamaica', 'Cuba', 'Zimbabwe', 'Botswana', 'Namibia', 'Senegal',
       'Mali', 'Mauritania', 'Benin', 'Niger', 'Nigeria', 'Cameroon',
       'Togo', 'Ghana', "Côte d'Ivoire", 'Guinea', 'Guinea-Bissau',
       'Liberia', 'Sierra Leone', 'Burkina Faso', 'Central African Rep.',
       'Congo', 'Gabon', 'Eq. Guinea', 'Zambia', 'Malawi', 'M

In [31]:
##checking country name not present in world data
set(df['country'].unique())-set(world['name'].unique())

{'Antigua and Barbuda',
 'Aruba',
 'Bahrain',
 'Barbados',
 'Bosnia and Herzegovina',
 'Cabo Verde',
 'Czech Republic',
 'Dominica',
 'Grenada',
 'Kiribati',
 'Macau',
 'Maldives',
 'Malta',
 'Mauritius',
 'Republic of Korea',
 'Russian Federation',
 'Saint Kitts and Nevis',
 'Saint Lucia',
 'Saint Vincent and Grenadines',
 'San Marino',
 'Seychelles',
 'Singapore',
 'United States'}

In [32]:
# renaming countries to merge with world data
df['country']=np.where(df['country']=='Russian Federation','Russia',df['country'])
df['country']=np.where(df['country']=='Republic of Korea','South Korea',df['country'])
df['country']=np.where(df['country']=='United States','United States of America',df['country'])
df['country']=np.where(df['country']=='Dominica','Dominican Rep.',df['country'])


In [33]:
#df['country'].unique()

In [34]:
country_level_agg=df.pivot_table(index=['country'],values=['suicides_no','population',' gdp_for_year ($) '],aggfunc={'suicides_no':sum,'population':sum,' gdp_for_year ($) ':sum}).reset_index()
country_level_agg.head()

country   gdp_for_year ($)   population  suicides_no
0              Albania       1375878560004    62325467         1970
1  Antigua and Barbuda        260348650212     1990228           11
2            Argentina     102023417116356  1035985431        82219
3              Armenia       1605204468992    77348173         1905
4                Aruba        368965541916     1259677          101

In [35]:
country_level_agg['suicides per 100k people']=np.round(country_level_agg['suicides_no']*100000/country_level_agg['population'],2)

country_level_agg['gdp per capita($)']=np.round((country_level_agg[' gdp_for_year ($) ']/country_level_agg['population']).astype(float),0)

country_level_agg.head()


country   gdp_for_year ($)   population  suicides_no  \
0              Albania       1375878560004    62325467         1970   
1  Antigua and Barbuda        260348650212     1990228           11   
2            Argentina     102023417116356  1035985431        82219   
3              Armenia       1605204468992    77348173         1905   
4                Aruba        368965541916     1259677          101   

   suicides per 100k people  gdp per capita($)  
0                      3.16            22076.0  
1                      0.55           130813.0  
2                      7.94            98480.0  
3                      2.46            20753.0  
4                      8.02           292905.0

In [36]:
print(country_level_agg.shape)
print(world.shape)

(101, 6)
(177, 6)


In [37]:
world=pd.merge(world,country_level_agg,left_on=['name'],right_on=['country'],how='left')

In [38]:
world.isna().sum()

pop_est                      0
continent                    0
name                         0
iso_a3                       0
gdp_md_est                   0
geometry                     0
country                     95
 gdp_for_year ($)           95
population                  95
suicides_no                 95
suicides per 100k people    95
gdp per capita($)           95
dtype: int64

In [39]:
## plotting map with folium
urban_area_map = folium.Map( location=[0, 0],zoom_start=2.2)
title_html = '''
             <h3 align="center" style="font-size:20px"><b>Suicides by Country </b></h3>
             <h6 align="center" style="font-size:14px"><b>1985-2016 </b></h6>
             '''
urban_area_map.get_root().html.add_child(folium.Element(title_html))
folium.Choropleth(
    geo_data=world,
    name='choropleth',
    data=world,
    columns=['name', 'suicides per 100k people'],
    key_on='feature.properties.name',
    fill_color='YlOrRd',
    nan_fill_color='White',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Suicides per 100k People'
).add_to(urban_area_map)

In [40]:
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}
NIL = folium.features.GeoJson(
    world,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['name', 'suicides per 100k people'],
        aliases=['Country: ','Suicides per 100k people: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
urban_area_map.add_child(NIL)
urban_area_map.keep_in_front(NIL)
folium.LayerControl().add_to(urban_area_map)
urban_area_map

#### Country level stats with gender and age

In [41]:
icountry_level_agg = country_level_agg.interactive()

In [42]:
country_level_agg_pipeline = (
    icountry_level_agg
    .groupby(['country'])['suicides per 100k people'].mean()
    .to_frame()
    .reset_index()
    .sort_values(by=['suicides per 100k people'])  
    .reset_index(drop=True)
)



In [43]:
country_level_agg_plot=country_level_agg_pipeline.hvplot.barh(x='country', y='suicides per 100k people',title="Suicides by Country 1985-2016",
                  rot=0, width=1000,height=1200,cmap='Pastel2',legend=False,color='country')
country_level_agg_plot

In [44]:
country_gender_year_pipeline = (
    idf[
        (idf.year <= year_slider)&(idf.suicides_no>0)
    ]
    .groupby(['country', 'sex'])['suicides_no'].sum().rename("Percentage of total Suicide").groupby(level = 0).transform(lambda x: 100*x/x.sum())
    .to_frame()
    .reset_index()
    .sort_values(by=['country','sex'])  
    .reset_index(drop=True)
)


In [45]:
country_gender_year_pipeline.head()

In [46]:
country_gender_year_plot=country_gender_year_pipeline.hvplot.barh(x='country', by='sex',y='Percentage of total Suicide',cmap='Pastel2',
                 stacked=True, rot=0, width=1000,legend='top',height=1200,title="Suicides by Country & Gender 1985-2016")
country_gender_year_plot

In [47]:
country_age_year_pipeline = (
    idf[
        (idf.year <= year_slider)&(idf.suicides_no>0)
    ]
    .groupby(['country', 'age'])['suicides_no'].sum().rename("Percentage of total Suicide").groupby(level = 0).transform(lambda x: 100*x/x.sum())
    .to_frame()
    .reset_index()
    .sort_values(by=['country','age'])  
    .reset_index(drop=True)
)


In [48]:
country_age_year_pipeline.head()

In [49]:
country_age_year_plot=country_age_year_pipeline.hvplot.barh(x='country', by='age',y='Percentage of total Suicide',cmap='Pastel2',
                 stacked=True, rot=0, width=1000,legend='top',height=1200,title="Suicides by Country & Age 1985-2016",)
country_age_year_plot

#### overall gender and age suicide rate/100k

In [50]:
world_age_pipeline = (
    idf
    .groupby(['age'])['suicides/100k pop'].mean().rename("% Suicides per 100k People").transform(lambda x: 100*x/x.sum())
    .to_frame()
    .reset_index()
    .sort_values(by=['% Suicides per 100k People'])  
    .reset_index(drop=True)
)


In [51]:
world_age_pipeline_plot=world_age_pipeline.hvplot.bar(x='age',y='% Suicides per 100k People',cmap='Pastel1',
                  rot=45, width=500,height=250,title="Age wise %Suicides per 100k: 1985-2016",legend=False,color='age')
world_age_pipeline_plot

In [52]:
world_gender_pipeline = (
    idf
    .groupby(['sex'])['suicides/100k pop'].mean().rename("% Suicides per 100k People").transform(lambda x: 100*x/x.sum())
    .to_frame()
    .reset_index()
    .sort_values(by=['sex'])  
    .reset_index(drop=True)
)


In [53]:
world_gender_pipeline_plot=world_gender_pipeline.hvplot.bar(x='sex',y='% Suicides per 100k People',cmap='Pastel2',
                  rot=0, width=500,height=250,title="Gender wise %Suicides per 100k: 1985-2016",legend=False,color='sex')
world_gender_pipeline_plot

## select widget to select country name

In [54]:
country_list=list(df['country'].unique())

In [55]:
# create widget
select = pn.widgets.Select(name='Select Country', options=country_list)


In [56]:
country_year_pipeline = (
    idf[(idf['country']==select)&(idf['year']<= year_slider)]
    .groupby(['year'])['suicides/100k pop'].mean().rename("Suicides per 100k People").transform(lambda x: round(x,2))
    .to_frame()
    .reset_index()
    .sort_values(by=['year'])  
    .reset_index(drop=True)
)


In [57]:
country_year_pipeline

In [58]:
country_year_pipeline.hvplot.table(width=500)

In [59]:
country_stats=pn.panel(country_year_pipeline.hvplot.table(width=500,title="Data Table")+country_year_pipeline.hvplot.line(x='year',y='Suicides per 100k People',cmap='Pastel2',
                  rot=0, width=800,height=400,title="Avg Suicides per 100k people",legend=False))

In [60]:
country_stats

Interactive(Interactive)

In [61]:
# create widget
tabs = pn.Tabs()#(background='White')
tabs.extend([('Worldwide Suicides & GDP per capita',world_year_pipeline_plot),
             ('By Gender Worldwide Suicides & GDP per capita',world_year_gender_pipeline),
            ('By Age Worldwide Suicides & GDP per capita',world_year_age_pipeline)
            ])

tabs2 = pn.Tabs()
tabs2.extend([('Country wise Suicide per 100k People',country_level_agg_plot),
             ('Suicides by Country & Gender',country_gender_year_plot),
            ('Suicides by Country & Age',country_age_year_plot)
            ])



In [62]:
tabs

Tabs
    [0] Interactive(Interactive, name='Worldwide Suicides &...)
    [1] Interactive(Interactive, name='By Gender Worldwide S...)
    [2] Interactive(Interactive, name='By Age Worldwide S...)

In [63]:
pn.Column(
    pn.Row(pn.Column(tabs),pn.Column(pn.Row(world_gender_pipeline_plot),pn.Row(world_age_pipeline_plot))),
    pn.Spacer(width=50),
    pn.Row(pn.panel(urban_area_map,height=600)),
    pn.Row(country_stats),
    pn.Row(tabs2),width_policy='max', height_policy='max'
)

Column(height_policy='max', width_policy='max')
    [0] Row
        [0] Column
            [0] Tabs
                [0] Interactive(Interactive, name='Worldwide Suicides &...)
                [1] Interactive(Interactive, name='By Gender Worldwide S...)
                [2] Interactive(Interactive, name='By Age Worldwide S...)
        [1] Column
            [0] Row
                [0] Interactive(Interactive)
            [1] Row
                [0] Interactive(Interactive)
    [1] Spacer(width=50)
    [2] Row
        [0] Folium(Map, height=600)
    [3] Row
        [0] Interactive(Interactive)
    [4] Row
        [0] Tabs
            [0] Interactive(Interactive, name='Country wise S...)
            [1] Interactive(Interactive, name='Suicides by C...)
            [2] Interactive(Interactive, name='Suicides by C...)

### creating dashboard

In [64]:
#Layout using Template
template = pn.template.FastListTemplate(
    title='Suicide Rates Overview 1985 to 2016', 
    sidebar=[pn.pane.Markdown("# World Suicide dashboard 1985-2016"), 
             pn.pane.Markdown("####This compiled dataset pulled from four other datasets linked by time and place, and was built to find signals correlated to increased suicide rates among different cohorts globally, across the socio-economic spectrum."), 
             pn.pane.PNG('climate_day.png', sizing_mode='scale_both'),
            ],
    main=[
    pn.Row(tabs,pn.Column(world_gender_pipeline_plot,world_age_pipeline_plot),background='White'),
    #pn.Spacer(width=50),
    pn.Row(pn.panel(urban_area_map,height=600),background='White'),
    pn.Row(country_stats,background='White',width=1600),
    pn.Row(tabs2,background='White',width=1600,scroll=True,height=600)
    ],
    accent_base_color="#88d8b0",
    header_background="#88d8b0",
)

In [65]:
#template.show()
template.servable();